In [15]:
import rasterio
from rasterstats import zonal_stats
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib.pyplot as plt
import json
import folium
from rasterio.mask import mask
from shapely.geometry import mapping
from branca.element import Template, MacroElement


In [3]:
raster_data = '2019_Nature_Africa_Housing_2015_NGA.tiff'
with rasterio.open(raster_data) as src:
    raster_crs = src.crs
    raster_bounds = src.bounds
    print("Raster CRS:", raster_crs)
    print("Raster bounds:", raster_bounds)

Raster CRS: EPSG:4326
Raster bounds: BoundingBox(left=2.6665935999999983, bottom=4.2499742999999945, right=14.666588799999996, top=13.916637099999996)


In [4]:
gdf = gpd.read_file('gadm36_NGA_1.shp')

# matching crs of raster file and geodataframe
gdf.set_crs(epsg=4326, inplace=True)
gdf = gdf.to_crs(raster_crs)

# Compute zonal statistics
stats = zonal_stats(gdf, raster_data, stats='mean', nodata=-9999)

# Add the statistics to the GeoDataFrame
gdf['housing_percentage'] = [stat['mean'] for stat in stats]

C:\Users\catch\anaconda3\lib\site-packages\numpy\core\_methods.py:48: RuntimeWarning: overflow encountered in reduce
  return umr_sum(a, axis, dtype, out, keepdims, initial, where)
C:\Users\catch\anaconda3\lib\site-packages\numpy\core\_methods.py:48: RuntimeWarning: overflow encountered in reduce
  return umr_sum(a, axis, dtype, out, keepdims, initial, where)
C:\Users\catch\anaconda3\lib\site-packages\numpy\core\_methods.py:48: RuntimeWarning: overflow encountered in reduce
  return umr_sum(a, axis, dtype, out, keepdims, initial, where)
C:\Users\catch\anaconda3\lib\site-packages\numpy\core\_methods.py:48: RuntimeWarning: overflow encountered in reduce
  return umr_sum(a, axis, dtype, out, keepdims, initial, where)
C:\Users\catch\anaconda3\lib\site-packages\numpy\core\_methods.py:48: RuntimeWarning: overflow encountered in reduce
  return umr_sum(a, axis, dtype, out, keepdims, initial, where)
C:\Users\catch\anaconda3\lib\site-packages\numpy\core\_methods.py:48: RuntimeWarning: overflow 

In [16]:

raster_file_path = '2019_Nature_Africa_Housing_2015_NGA.tiff'
shapefile_path = 'gadm36_NGA_1.shp'

# Load the shapefile
states = gpd.read_file(shapefile_path)

# Initializing a list to store average values
average_values = []

# Open the raster file
with rasterio.open(raster_file_path) as src:
    for state in states.itertuples():
        # Create a mask for the current state
        state_geom = state.geometry
        out_image, out_transform = mask(src, [mapping(state_geom)], crop=True)
        
        
        out_image = out_image[0]  #single-band raster
        valid_data = out_image[out_image > 0]  # Assuming 0 is invalid or no data
        
        # Calculate average value for  state
        if valid_data.size > 0:
            average_value = np.mean(valid_data)
        else:
            average_value = np.nan
        
        # Append the result to the list
        average_values.append(average_value)

# Add average values to the GeoDataFrame
states['avg_housing_quality'] = average_values



# Convert GeoDataFrame to GeoJSON
geo_json = states.to_json()
geo_json_data = json.loads(geo_json)

# Nigeria
m = folium.Map(location=[9.0820, 8.6753], zoom_start=6)

#  styling the features based on average housing quality
def style_function(feature):
    avg_quality = feature['properties'].get('avg_housing_quality', 0)  # Default to 0 if the key is missing
    if avg_quality > .40:
        color = '#006400'  # Dark Green
    elif avg_quality > .20:
        color = '#9ACD32'  # Yellow Green
    elif avg_quality > .10:
        color = '#FFD700'  # Gold
    else:
        color = '#FF4500'  # Orange Red
    return {
        'fillColor': color,
        'color': 'black',
        'weight': 1.5,
        'fillOpacity': 0.6,
    }

# Add the GeoJSON to the map with styling
folium.GeoJson(
    geo_json_data,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['avg_housing_quality'], 
        aliases=['Average Housing Quality:']
    )
).add_to(m)

legend_html = '''
{% macro html(this, kwargs) %}
<div style="
    position: fixed; 
    bottom: 50px; left: 50px; width: 200px; height: 150px; 
    background-color: white; z-index:9999; font-size:14px;
    border:2px solid grey; padding: 10px; 
    ">
    <h4>Average Housing Quality</h4>
    <i style="background: #006400; width: 18px; height: 18px; float: left; margin-right: 8px;"></i> > 0.40<br>
    <i style="background: #9ACD32; width: 18px; height: 18px; float: left; margin-right: 8px;"></i> 0.20 - 0.40<br>
    <i style="background: #FFD700; width: 18px; height: 18px; float: left; margin-right: 8px;"></i> 0.10 - 0.20<br>
    <i style="background: #FF4500; width: 18px; height: 18px; float: left; margin-right: 8px;"></i> 0.00 - 0.10<br>
</div>
{% endmacro %}
'''

macro = MacroElement()
macro._template = Template(legend_html)
m.get_root().add_child(macro)

m

North Nigeria has more below average housing quality and improves as we move south. Imo has the best housing quality. 